In [0]:
import random
from pyspark.ml.clustering import KMeans
from pyspark.ml.evaluation import ClusteringEvaluator
import matplotlib.pyplot as plt
from pyspark.sql import functions as F
from pyspark.sql.functions import col
import mlflow
import mlflow.spark
import pyspark
import time

In [0]:
version = '2_civ7'
model_name = 'campaign_clustering_turn_100'

source_table = f'sandbox.cg_inverness.{model_name}_data_v2_features_v{version}'

#--

k_max = 7
random_seed_count = 3
version=1
experiment_name = f'/Users/jak.marshall@2k.com/Kmeans_turn_100_PCA_v2_{version}'

print(f'source_table:      {source_table}')
print(f'experiment_name:   {experiment_name}')


source_table:      sandbox.cg_inverness.campaign_clustering_turn_100_data_v2_features_v2_civ7
experiment_name:   /Users/jak.marshall@2k.com/Kmeans_turn_100_PCA_v2_1


In [0]:
df = spark.table(source_table)
df.limit(5).toPandas()

features                       CAMPAIGN_ID
0  (0.5885875074807524, 0.965700179519515, 0.3144...  414a180b6904bbcf54c54a2bdccbf6ad
1  (0.0, 0.3219000598398383, 0.6288079734362841, ...  11f0d5e476e68256f43c2621e400978f
2  (0.8828812612211285, 0.3219000598398383, 0.419...  4ed7e07c53537bde06a7ebcd2c172191
3  (0.2942937537403762, 0.4828500897597575, 0.628...  45c3dedc39afb9eda415e3643b28a5b5
4  (0.8828812612211285, 0.4828500897597575, 0.209...  4353676d55133ebc418ae4f9c761e8ad

In [0]:
from pyspark.sql.functions import size

num_rows = df.count()
num_columns = df[['features']].schema["features"].metadata["ml_attr"]["num_attrs"]
print("Number of rows:", num_rows)
print("Number of columns:", num_columns)

Number of rows: 529282
Number of columns: 56


In [0]:
from pyspark.ml.feature import PCA

pca = PCA(k=21, inputCol="features")
pca.setOutputCol("pca_features")

model = pca.fit(df[['features']])

sum(model.explainedVariance)

np.float64(0.9033711508011085)

In [0]:
model.setOutputCol("output")

transformed_features=model.transform(df)

In [0]:
display(transformed_features)

features CAMPAIGN_ID output Map(vectorType -> sparse, length -> 56, indices -> List(0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 18, 19, 21, 24, 33, 38, 45, 48, 52), values -> List(0.5885875074807524, 0.965700179519515, 0.31440398671814207, 1.6022970765200626, 1.8200478829342412, 5.5277310393881685, 1.302246221614133, 1.658493113181259, 2.588085580408564, 2.231726823489336, 1.3857259613269053, 1.496000183900265, 1.917831588389217, 0.6543800371290599, 1.2025101442095685, 2.0855550977392654, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0)) 414a180b6904bbcf54c54a2bdccbf6ad Map(vectorType -> dense, length -> 21, values -> List(-4.628801639618975, -4.226169662353111, 0.9617293509130748, 1.0021172060995274, -1.7440987466120115, 4.426444778025937, -0.10193919818515326, -0.5097866063389163, -0.24065919286454274, -0.7472672446119425, -0.17374395350017977, 0.9526608133548193, -0.20480703048334034, -0.36575145221982686, -0.504384250358586, 1.1701185391911892, 1.473329371433017, 0.6289210262684284, -0.91956263548686, -0.12922437736192077, -0.2968059921089431)) Map(vectorType -> sparse, length -> 56, indices -> List(1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 14, 15, 16, 18, 19, 23, 34, 38, 45, 47, 52), values -> List(0.3219000598398383, 0.6288079734362841, 1.4247025729648832, 0.3493841918132695, 4.606442532823474, 2.9442088488667357, 2.3277096325351003, 2.588085580408564, 2.510692676425503, 2.103334048442624, 2.0262280971813715, 0.6973933048688061, 0.5712187682598089, 0.27697164154964754, 0.3950234422698009, 0.6543800371290599, 1.2025101442095685, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0)) 11f0d5e476e68256f43c2621e400978f Map(vectorType -> dense, length -> 21, values -> List(-4.6850543781962415, -4.499950198787214, 1.3142136434376506, 4.1796136571639955E-4, 0.9164517959972958, 2.263663808867489, -0.00857647015483234, -0.9779584472929409, -1.0904317466244617, -0.9395594324673288, -0.43533099570126255, 1.3121144306830506, 0.39612868543078117, 0.046662182733302165, 0.28143963959659224, 2.7857803902410385, 0.6094056257279351, -0.04423153421891168, -1.4080342182037122, -0.10827605722685724, 0.07347216219885994)) Map(vectorType -> sparse, length -> 56, indices -> List(0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 14, 17, 18, 19, 21, 23, 33, 40, 45, 47, 53), values -> List(0.8828812612211285, 0.3219000598398383, 0.41920531562418945, 1.2115891686986682, 0.6215788528770958, 4.606442532823474, 2.887589447926991, 2.9387334110755643, 5.6075187575518886, 2.324715441134725, 4.8747859710964345, 2.5943294328396997, 3.4433794427897304, 0.011900391005412684, 0.9606863850570947, 1.6359500928226498, 0.4509413040785882, 2.0855550977392654, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0)) 4ed7e07c53537bde06a7ebcd2c172191 Map(vectorType -> dense, length -> 21, values -> List(-6.943745629867604, -7.449101701768911, 0.07254897675457558, -0.2841903030311495, -0.541597293923995, 3.11289198960197, 1.1254066605505528, 1.338425445568376, 0.19826486850746325, -0.48048532170161645, -0.7340604801982427, -0.42261287578374224, -0.01692500534263796, 0.8150538039777552, -0.31499829536943164, 1.4676461193328538, 0.46855224424088304, -1.3098782710935815, -1.7532026751161538, -1.2622789825294014, -0.006764620935425764)) Map(vectorType -> sparse, length -> 56, indices -> List(0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 23, 33, 44, 45, 49, 52), values -> List(0.2942937537403762, 0.4828500897597575, 0.6288079734362841, 1.229348619054186, 2.0841173302349683, 5.5277310393881685, 2.661111844168011, 2.269516891721723, 4.744823564082367, 1.952760970553169, 1.039294470995179, 1.7800508517294291, 2.528050730149422, 0.48463683915741534, 0.14280469206495222, 0.27697164154964754, 0.16459310094575036, 0.5764118310342569, 0.6543800371290599, 0.4509413040785882, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0)) 45c3dedc39afb9eda415e3643b28a5b5 Map(vectorType -> dense, length -> 21, values -> List(-5.164776566411206, -5.2226536737636975, 1.2471520138014798, 1.2723522089365793, 0.950085687660685, 4.546072775902652, 2.0634382927182586, -0.300665014

In [0]:
model_name = 'campaign_clustering_turn_100'
versionpca = '2_civ7'

target_table = f'sandbox.cg_inverness.{model_name}_data_v2_features_v2_PCA_v{versionpca}'

print(f'target_table: {target_table}')

(transformed_features[['output','CAMPAIGN_ID']]
 .write
 .format("delta")
 .mode("overwrite")
 .option("overwriteSchema", "true")
 .saveAsTable(target_table))

target_table: sandbox.cg_inverness.campaign_clustering_turn_100_data_v2_features_v2_PCA_v2_civ7
